# #                                              Modelling

In [1]:
#importing libraries

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.ticker as ticker
import matplotlib.ticker as plticker
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification

In [2]:
#load data 

world_cup = pd.read_csv('T20TeamStats.csv')
results = pd.read_csv('T20Records.csv')
ranks = pd.read_csv('T20Ranking.csv')

In [3]:
world_cup.head()

Team Group  Previous Appearances  Previous Titles  Previous Finals  \
0    Canada     A                     0                0                0   
1     India     A                     8                1                2   
2   Ireland     A                     7                0                0   
3  Pakistan     A                     8                1                3   
4    U.S.A.     A                     0                0                0   

   Previous Semifinals  Current Ranking  
0                    0               23  
1                    4                1  
2                    0               11  
3                    6                7  
4                    0               19

In [4]:
# Previous records
results

Date         Team1         Team2       Winner         Venue
0      2/17/2005   New Zealand     Australia    Australia      Auckland
1      6/13/2005       England     Australia      England   Southampton
2     10/21/2005  South Africa   New Zealand  New Zealand  Johannesburg
3       1/9/2006     Australia  South Africa    Australia      Brisbane
4      2/16/2006   New Zealand   West Indies         tied      Auckland
...          ...           ...           ...          ...           ...
2607   5/12/2024    Bangladesh      Zimbabwe     Zimbabwe        Mirpur
2608   5/12/2024         Japan      Mongolia        Japan          Sano
2609   5/14/2024       Ireland      Pakistan     Pakistan        Dublin
2610   5/18/2024   Netherlands      Scotland  Netherlands     The Hague
2611   5/19/2024   Netherlands       Ireland      Ireland     The Hague

[2612 rows x 5 columns]

In [5]:
#Removing the record with ties
data=results[results.Winner!='tied']

In [6]:
# Dropping Venue column ,Since Only Australia will host the World Cup so home team advantage not possible for other team
data.drop(columns=['Venue'],inplace=True)

C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\1552488147.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.drop(columns=['Venue'],inplace=True)


In [7]:
#Dropping the date column
data.drop(columns=['Date'],inplace=True)
data.head()

C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\1784127581.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.drop(columns=['Date'],inplace=True)


Team1         Team2        Winner
0   New Zealand     Australia     Australia
1       England     Australia       England
2  South Africa   New Zealand   New Zealand
3     Australia  South Africa     Australia
5  South Africa     Australia  South Africa

In [9]:
#Filtering the records for only teams that will play the world cup
worldcup_teams = ['South Africa','India','England','New Zealand','Bangladesh','Australia','Pakistan','Canada',
                  'Sri Lanka','Ireland','Netherlands','West Indies','Afghanistan','Nepal','Oman','U.S.A.','P.N.G.',
                  'Namibia','Uganda','Scotland']
df_teams_1 = data[data['Team1'].isin(worldcup_teams)]
df_teams_2 = data[data['Team2'].isin(worldcup_teams)]
df_teams = pd.concat((df_teams_1, df_teams_2))
df_teams.drop_duplicates()
df_teams.count()

Team1     2602
Team2     2602
Winner    2602
dtype: int64

In [10]:
#Adding column 'Count': It will record the team which won the most matches from its previous 6 matches (i.e. if India have won 4 matches from its previous 6 matches and Pakistan have won 3 matches than count which select India)
# and 'Rank': The team which is having higher rank will be named in this column
df_teams['Count']=0
df_teams['Rank']=0
df_team= df_teams.reset_index(drop=True) 
df_team

Team1         Team2        Winner  Count  Rank
0      New Zealand     Australia     Australia      0     0
1          England     Australia       England      0     0
2     South Africa   New Zealand   New Zealand      0     0
3        Australia  South Africa     Australia      0     0
4     South Africa     Australia  South Africa      0     0
...            ...           ...           ...    ...   ...
2597       Ireland      Pakistan       Ireland      0     0
2598       Ireland      Pakistan      Pakistan      0     0
2599       Ireland      Pakistan      Pakistan      0     0
2600   Netherlands      Scotland   Netherlands      0     0
2601   Netherlands       Ireland       Ireland      0     0

[2602 rows x 5 columns]

In [15]:
# Assuming df_team and ranks DataFrames are already defined and imported

# Ensure 'Count' and 'Rank' columns exist in the DataFrame
df_team['Count'] = ""
df_team['Rank'] = ""

# Iterate over each row
for i in range(2602):
    dt1 = df_team['Team1'].iloc[i].strip()
    dt2 = df_team['Team2'].iloc[i].strip()
    c1 = c2 = w1 = w2 = 0

    # Check for the next 50 matches
    for j in range(i+1, min(i+51, len(df_team))):
        if ((df_team['Team1'].iloc[j].strip() == dt1) or (df_team['Team2'].iloc[j].strip() == dt1)) and c1 < 6:
            c1 += 1
            if df_team['Winner'].iloc[j].strip() == dt1:
                w1 += 1
        
        if ((df_team['Team1'].iloc[j].strip() == dt2) or (df_team['Team2'].iloc[j].strip() == dt2)) and c2 < 6:
            c2 += 1
            if df_team['Winner'].iloc[j].strip() == dt2:
                w2 += 1

    # Assign 'Count' based on the wins
    df_team.loc[i, 'Count'] = dt2 if w2 > w1 else dt1

    # Retrieve ranks for both teams
    r1 = ranks.loc[ranks['Team'] == dt1, 'Rank'].values[0] if not ranks.loc[ranks['Team'] == dt1, 'Rank'].empty else float('inf')
    r2 = ranks.loc[ranks['Team'] == dt2, 'Rank'].values[0] if not ranks.loc[ranks['Team'] == dt2, 'Rank'].empty else float('inf')

    # Assign 'Rank' based on the comparison
    df_team.loc[i, 'Rank'] = dt1 if r2 > r1 else dt2


In [16]:
data=df_team.iloc[0:2602]
data

Team1         Team2        Winner         Count          Rank
0      New Zealand     Australia     Australia   New Zealand     Australia
1          England     Australia       England     Australia     Australia
2     South Africa   New Zealand   New Zealand  South Africa  South Africa
3        Australia  South Africa     Australia  South Africa     Australia
4     South Africa     Australia  South Africa  South Africa     Australia
...            ...           ...           ...           ...           ...
2597       Ireland      Pakistan       Ireland      Pakistan      Pakistan
2598       Ireland      Pakistan      Pakistan       Ireland      Pakistan
2599       Ireland      Pakistan      Pakistan       Ireland      Pakistan
2600   Netherlands      Scotland   Netherlands   Netherlands   Netherlands
2601   Netherlands       Ireland       Ireland   Netherlands       Ireland

[2602 rows x 5 columns]

In [17]:
#Assigning the binary number to data , team1: 0 and team2: 1
for i in range(2602):
    dt1=data['Team1'].iloc[i]
    dt2=data['Team2'].iloc[i]
    data['Team1'].iloc[i]=0
    data['Team2'].iloc[i]=1
    if data['Winner'].iloc[i]==dt1.strip():
        data['Winner'].iloc[i]=data['Team1'].iloc[i]
    else:
        data['Winner'].iloc[i]=data['Team2'].iloc[i]
    
    if data['Count'].iloc[i]==dt1:
        data['Count'].iloc[i]=data['Team1'].iloc[i]
    else:
        data['Count'].iloc[i]=data['Team2'].iloc[i]
    
    if data['Rank'].iloc[i]==dt1:
        data['Rank'].iloc[i]=data['Team1'].iloc[i]
    else:
        data['Rank'].iloc[i]=data['Team2'].iloc[i]
        
    
        

C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\1952454237.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Team1'].iloc[i]=0
C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\1952454237.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Team2'].iloc[i]=1
C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\1952454237.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Winner'].iloc[i]=data['Team2'].iloc[i]
C:\Users\Hp\AppDat

In [18]:
data

Team1 Team2 Winner Count Rank
0        0     1      1     0    1
1        0     1      0     1    1
2        0     1      1     0    0
3        0     1      0     1    0
4        0     1      0     0    1
...    ...   ...    ...   ...  ...
2597     0     1      0     1    1
2598     0     1      1     0    1
2599     0     1      1     0    1
2600     0     1      0     0    0
2601     0     1      1     0    1

[2602 rows x 5 columns]

In [21]:
#importing the fixture file of upcoming world cup
fixtures = pd.read_csv('T20Fixture.csv')
fixtures

Date         Team1         Team2         Group  \
0    6/1/2024        U.S.A.        Canada       Group A   
1    6/5/2024         India       Ireland       Group A   
2    6/6/2024        U.S.A.      Pakistan       Group A   
3    6/7/2024        Canada       Ireland       Group A   
4    6/9/2024         India      Pakistan       Group A   
5   6/11/2024      Pakistan        Canada       Group A   
6   6/12/2024        U.S.A.         India       Group A   
7   6/14/2024        U.S.A.       Ireland       Group A   
8   6/15/2024         India        Canada       Group A   
9   6/16/2024      Pakistan       Ireland       Group A   
10   6/2/2024       Namibia          Oman       Group B   
11   6/4/2024       England      Scotland       Group B   
12   6/5/2024     Australia          Oman       Group B   
13   6/6/2024       Namibia      Scotland       Group B   
14   6/8/2024     Australia       England       Group B   
15   6/9/2024          Oman      Scotland       Group B   
16  6/11/2024     Australia       Namibia       Group B   
17  6/13/2024       England          Oman       Group B   
18  6/15/2024       Namibia       England       Group B   
19  6/15/2024     Australia      Scotland       Group B   
20   6/2/2024   West Indies        P.N.G.       Group C   
21   6/3/2024   Afghanistan        Uganda       Group C   
22   6/5/2024        P.N.G.        Uganda       Group C   
23   6/7/2024   New Zealand   Afghanistan       Group C   
24   6/8/2024   West Indies        Uganda       Group C   
25  6/12/2024   West Indies   New Zealand       Group C   
26  6/13/2024   Afghanistan        P.N.G.       Group C   
27  6/14/2024   New Zealand        Uganda       Group C   
28  6/17/2024   New Zealand        P.N.G.       Group C   
29  6/17/2024   West Indies   Afghanistan       Group C   
30   6/3/2024     Sri Lanka  South Africa       Group D   
31   6/4/2024   Netherlands         Nepal       Group D   
32   6/7/2024     Sri Lanka    Bangladesh       Group D   
33   6/8/2024   Netherlands  South Africa       Group D   
34  6/10/2024  South Africa    Bangladesh       Group D   
35  6/11/2024     Sri Lanka         Nepal       Group D   
36  6/13/2024    Bangladesh   Netherlands       Group D   
37  6/14/2024  South Africa         Nepal       Group D   
38  6/16/2024    Bangladesh         Nepal       Group D   
39  6/16/2024     Sri Lanka   Netherlands       Group D   
40  6/19/2024            A2            D1       Group 2   
41  6/19/2024            B1            C2       Group 2   
42  6/20/2024            C1            A1       Group 1   
43  6/20/2024            B2            D2       Group 1   
44  6/21/2024            B1            D1       Group 2   
45  6/21/2024            A2            C2       Group 2   
46  6/22/2024            A1            D2       Group 1   
47  6/22/2024            C1            B2       Group 1   
48  6/23/2024            A2            B1       Group 2   
49  6/23/2024            C2            D1       Group 2   
50  6/24/2024            B2            A1       Group 1   
51  6/24/2024            C1            D1       Group 1   
52  6/26/2024           TBD           TBD  Semi-final 1   
53  6/27/2024           TBD           TBD  Semi-final 2   
54  6/29/2024           TBD           TBD         Final   

                               Venue      Country  Result  
0                             Dallas       U.S.A.     NaN  
1                           New York       U.S.A.     NaN  
2                             Dallas       U.S.A.     NaN  
3                           New York       U.S.A.     NaN  
4                           New York       U.S.A.     NaN  
5                           New York       U.S.A.     NaN  
6                           New York       U.S.A.     NaN  
7                         Lauderhill       U.S.A.     NaN  
8                         Lauderhill       U.S.A.     NaN  
9                         Lauderhill       U.S.A.     NaN  
10                          Barbados  West-I

In [34]:
#selecting the record till League matches
fixtures=fixtures.iloc[0:40]
fixtures

Team1         Team2  Result
0         U.S.A.        Canada     NaN
1          India       Ireland     NaN
2         U.S.A.      Pakistan     NaN
3         Canada       Ireland     NaN
4          India      Pakistan     NaN
5       Pakistan        Canada     NaN
6         U.S.A.         India     NaN
7         U.S.A.       Ireland     NaN
8          India        Canada     NaN
9       Pakistan       Ireland     NaN
10       Namibia          Oman     NaN
11       England      Scotland     NaN
12     Australia          Oman     NaN
13       Namibia      Scotland     NaN
14     Australia       England     NaN
15          Oman      Scotland     NaN
16     Australia       Namibia     NaN
17       England          Oman     NaN
18       Namibia       England     NaN
19     Australia      Scotland     NaN
20   West Indies        P.N.G.     NaN
21   Afghanistan        Uganda     NaN
22        P.N.G.        Uganda     NaN
23   New Zealand   Afghanistan     NaN
24   West Indies        Uganda     NaN
25   West Indies   New Zealand     NaN
26   Afghanistan        P.N.G.     NaN
27   New Zealand        Uganda     NaN
28   New Zealand        P.N.G.     NaN
29   West Indies   Afghanistan     NaN
30     Sri Lanka  South Africa     NaN
31   Netherlands         Nepal     NaN
32     Sri Lanka    Bangladesh     NaN
33   Netherlands  South Africa     NaN
34  South Africa    Bangladesh     NaN
35     Sri Lanka         Nepal     NaN
36    Bangladesh   Netherlands     NaN
37  South Africa         Nepal     NaN
38    Bangladesh         Nepal     NaN
39     Sri Lanka   Netherlands     NaN

In [35]:
#Dropping the Date,Column1 and Venue columns
fixtures.drop(columns=['Date','Group','Venue','Country'],inplace=True)


KeyError: "['Date', 'Group', 'Venue', 'Country'] not found in axis"

In [36]:
#Seperating the output i.e. Winner column for testing model
y=data["Winner"]
y = y.astype(float, errors = 'raise')

In [37]:
#dropping the target column and creating features file
X=data.drop('Winner',axis=1)
X['Team1'] = X.Team1.astype(float)
X['Team2'] = X.Team2.astype(float)
X['Count'] = X.Count.astype(float)
X['Rank'] = X.Rank.astype(float)

In [38]:
#importing libraries for SVM(Support Vector Machine) model
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size= 0.2)

In [39]:
model = SVC(kernel = 'linear', C = 1)

In [40]:
model.fit(X_train, y_train)

SVC(C=1, kernel='linear')

In [41]:
svm_pred = model.predict(X_test)

In [42]:
#Accuracy score
accuracy = model.score(X_test, y_test)
accuracy

0.6314779270633397

In [43]:
U=fixtures.drop('Result',axis=1)
U['Count']=0
U['Rank']=0

In [44]:
U

Team1         Team2  Count  Rank
0         U.S.A.        Canada      0     0
1          India       Ireland      0     0
2         U.S.A.      Pakistan      0     0
3         Canada       Ireland      0     0
4          India      Pakistan      0     0
5       Pakistan        Canada      0     0
6         U.S.A.         India      0     0
7         U.S.A.       Ireland      0     0
8          India        Canada      0     0
9       Pakistan       Ireland      0     0
10       Namibia          Oman      0     0
11       England      Scotland      0     0
12     Australia          Oman      0     0
13       Namibia      Scotland      0     0
14     Australia       England      0     0
15          Oman      Scotland      0     0
16     Australia       Namibia      0     0
17       England          Oman      0     0
18       Namibia       England      0     0
19     Australia      Scotland      0     0
20   West Indies        P.N.G.      0     0
21   Afghanistan        Uganda      0     0
22        P.N.G.        Uganda      0     0
23   New Zealand   Afghanistan      0     0
24   West Indies        Uganda      0     0
25   West Indies   New Zealand      0     0
26   Afghanistan        P.N.G.      0     0
27   New Zealand        Uganda      0     0
28   New Zealand        P.N.G.      0     0
29   West Indies   Afghanistan      0     0
30     Sri Lanka  South Africa      0     0
31   Netherlands         Nepal      0     0
32     Sri Lanka    Bangladesh      0     0
33   Netherlands  South Africa      0     0
34  South Africa    Bangladesh      0     0
35     Sri Lanka         Nepal      0     0
36    Bangladesh   Netherlands      0     0
37  South Africa         Nepal      0     0
38    Bangladesh         Nepal      0     0
39     Sri Lanka   Netherlands      0     0

In [67]:
#We have assumped from recent performance of teams in qualifying matches that Group A winner : Sri Lanka
#Group A Runner Up : Namibia , Group B winner : West Indies and Group B runner Up : Scotland
  
for i in range(40):
    dt1=U['Team1'].iloc[i]
    dt2=U['Team2'].iloc[i]
    r1=0
    r2=0
    for k in range(40):
        if (dt1.strip()==ranks['Team'].iloc[k]):
            r1=ranks['Rank'].iloc[k]
        
    for k in range(40):
        if (dt2.strip()==ranks['Team'].iloc[k]):
            r2=ranks['Rank'].iloc[k]
        
    if(r2>r1):
        U['Rank'].iloc[i]=dt1
        U['Count'].iloc[i]=dt1
        
    else:
        U['Rank'].iloc[i]=dt2
        U['Count'].iloc[i]=dt2
        

        
    

AttributeError: 'numpy.float64' object has no attribute 'strip'

In [60]:
for i in range(40):
    dt1=U['Team1'].iloc[i]
    dt2=U['Team2'].iloc[i]
    U['Team1'].iloc[i]=0
    U['Team2'].iloc[i]=1
    if U['Count'].iloc[i]==dt1:
        U['Count'].iloc[i]=U['Team1'].iloc[i]
    else:
        U['Count'].iloc[i]=U['Team2'].iloc[i]
    
    if U['Rank'].iloc[i]==dt1:
        U['Rank'].iloc[i]=U['Team1'].iloc[i]
    else:
        U['Rank'].iloc[i]=U['Team2'].iloc[i]

C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\3088572261.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  U['Team1'].iloc[i]=0
C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\3088572261.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  U['Team2'].iloc[i]=1
C:\Users\Hp\AppData\Local\Temp\ipykernel_3984\3088572261.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  U['Count'].iloc[i]=U['Team2'].iloc[i]
C:\Users\Hp\AppData\Local\Temp\i

In [68]:
U

Team1  Team2  Count  Rank
0     0.0    1.0    1.0   1.0
1     0.0    1.0    1.0   1.0
2     0.0    1.0    1.0   1.0
3     0.0    1.0    1.0   1.0
4     0.0    1.0    1.0   1.0
5     0.0    1.0    1.0   1.0
6     0.0    1.0    1.0   1.0
7     0.0    1.0    1.0   1.0
8     0.0    1.0    1.0   1.0
9     0.0    1.0    1.0   1.0
10    0.0    1.0    1.0   1.0
11    0.0    1.0    1.0   1.0
12    0.0    1.0    1.0   1.0
13    0.0    1.0    1.0   1.0
14    0.0    1.0    1.0   1.0
15    0.0    1.0    1.0   1.0
16    0.0    1.0    1.0   1.0
17    0.0    1.0    1.0   1.0
18    0.0    1.0    1.0   1.0
19    0.0    1.0    1.0   1.0
20    0.0    1.0    1.0   1.0
21    0.0    1.0    1.0   1.0
22    0.0    1.0    1.0   1.0
23    0.0    1.0    1.0   1.0
24    0.0    1.0    1.0   1.0
25    0.0    1.0    1.0   1.0
26    0.0    1.0    1.0   1.0
27    0.0    1.0    1.0   1.0
28    0.0    1.0    1.0   1.0
29    0.0    1.0    1.0   1.0
30    0.0    1.0    1.0   1.0
31    0.0    1.0    1.0   1.0
32    0.0    1.0    1.0   1.0
33    0.0    1.0    1.0   1.0
34    0.0    1.0    1.0   1.0
35    0.0    1.0    1.0   1.0
36    0.0    1.0    1.0   1.0
37    0.0    1.0    1.0   1.0
38    0.0    1.0    1.0   1.0
39    0.0    1.0    1.0   1.0

In [69]:
U['Team1'] = U.Team1.astype(float)
U['Team2'] = U.Team2.astype(float)
U['Count'] = U.Count.astype(float)
U['Rank'] = U.Rank.astype(float)

In [70]:
#Appling SVM model on World Cup schedule
svm_pred = model.predict(U)

In [71]:
#Predicted vales 0: Team1 and 1:Team2
svm_pred

array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1.])

In [65]:
#Linking the predicted values with records
print("Results till League matches\n")
for i in range(40):
    if (svm_pred[i]==1.0):
        print(str(i+1)+"."+fixtures['Team1'].iloc[i] + " Vs " + fixtures['Team2'].iloc[i] + " : " + fixtures['Team2'].iloc[i] )
        print()
    else:
        print(str(i+1)+"."+fixtures['Team1'].iloc[i] + " Vs " + fixtures['Team2'].iloc[i] + " : " + fixtures['Team1'].iloc[i] )
        print()

Results till League matches

1.U.S.A. Vs Canada : Canada

2.India Vs Ireland : Ireland

3.U.S.A. Vs Pakistan : Pakistan

4.Canada Vs Ireland : Ireland

5.India Vs Pakistan : Pakistan

6.Pakistan Vs Canada : Canada

7.U.S.A. Vs India : India

8.U.S.A. Vs Ireland : Ireland

9.India Vs Canada : Canada

10.Pakistan Vs Ireland : Ireland

11.Namibia Vs Oman : Oman

12.England Vs Scotland : Scotland

13.Australia Vs Oman : Oman

14.Namibia Vs Scotland : Scotland

15.Australia Vs England : England

16.Oman Vs Scotland : Scotland

17.Australia Vs Namibia : Namibia

18.England Vs Oman : Oman

19.Namibia Vs England : England

20.Australia Vs Scotland : Scotland

21.West Indies Vs P.N.G. : P.N.G.

22.Afghanistan Vs Uganda : Uganda

23.P.N.G. Vs Uganda : Uganda

24.New Zealand Vs Afghanistan : Afghanistan

25.West Indies Vs Uganda : Uganda

26.West Indies Vs New Zealand : New Zealand

27.Afghanistan Vs P.N.G. : P.N.G.

28.New Zealand Vs Uganda : Uganda

29.New Zealand Vs P.N.G. : P.N.G.

30.West In

In [33]:
#Point table after league matches
print("From the Modelling the Point table as follows:\n")
print("Group 1\n")
print("Team\t\t\tWin")
print("Afghanistan\t\t0")
print("Australia\t\t3")
print("England\t\t\t4")
print("New Zealand\t\t4")
print("Group A Winner\t\t2")
print("Group B Runner Up\t2")
print("\nGroup 2\n")
print("Team\t\t\tWin")
print("Bangladesh\t\t0")
print("India\t\t\t5")
print("Pakistan\t\t4")
print("South Africa\t\t3")
print("Group B Winner\t\t2")
print("Group A Runner Up\t1")



From the Modelling the Point table as follows:

Group 1

Team			Win
Afghanistan		0
Australia		3
England			4
New Zealand		4
Group A Winner		2
Group B Runner Up	2

Group 2

Team			Win
Bangladesh		0
India			5
Pakistan		4
South Africa		3
Group B Winner		2
Group A Runner Up	1


In [34]:
V=U.iloc[18:20]
V['Count'].iloc[1]=0.0


c:\users\deswal\appdata\local\programs\python\python39\lib\site-packages\pandas\core\indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


In [35]:
#Predicting the semi-final winners
svm_pred = model.predict(V)

c:\users\deswal\appdata\local\programs\python\python39\lib\site-packages\sklearn\base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- Team_1
- Team_2
Feature names seen at fit time, yet now missing:
- Team1
- Team2

  warnings.warn(message, FutureWarning)


In [36]:
svm_pred


array([0., 0.])

In [37]:
print("Semi Finals\n")
print("India(0) Vs England(1) : India")
print("New Zealand(0) Vs Pakistan(1) : New Zealand")

Semi Finals

India(0) Vs England(1) : India
New Zealand(0) Vs Pakistan(1) : New Zealand


In [38]:
#Predicting the Final Winner
V=U.iloc[18:19]
svm_pred = model.predict(V)
svm_pred

c:\users\deswal\appdata\local\programs\python\python39\lib\site-packages\sklearn\base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- Team_1
- Team_2
Feature names seen at fit time, yet now missing:
- Team1
- Team2

  warnings.warn(message, FutureWarning)


array([0.])

In [39]:
print("Final\n")
print("India(0) Vs New Zealand(0) : India(0)\n")
print("Probable Winner of World Cup : India")

Final

India(0) Vs New Zealand(0) : India(0)

Probable Winner of World Cup : India
